In [1]:
import os
import pandas as pd
import plotly.express as px

folder_path = "./data"

# Get a list of all files in the folder
files = os.listdir(folder_path)

# Create an empty list to store the data from each file
data = {}

# Read each file into a pandas DataFrame and append it to the data list
for file in files:
    file_path = os.path.join(folder_path, file)
    df = pd.read_json(file_path, lines=True)
    data[file] = df

In [2]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots

In [3]:
for file, df in data.items():
    print(f"File: {file}")
    print(df.info())
    print()

File: artists.jsonl
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1667 entries, 0 to 1666
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   id      1667 non-null   object
 1   name    1667 non-null   object
 2   genres  1566 non-null   object
dtypes: object(3)
memory usage: 39.2+ KB
None

File: sessions.jsonl
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 759425 entries, 0 to 759424
Data columns (total 5 columns):
 #   Column      Non-Null Count   Dtype         
---  ------      --------------   -----         
 0   session_id  759425 non-null  int64         
 1   timestamp   759425 non-null  datetime64[ns]
 2   user_id     721555 non-null  float64       
 3   track_id    624016 non-null  object        
 4   event_type  721378 non-null  object        
dtypes: datetime64[ns](1), float64(1), int64(1), object(2)
memory usage: 29.0+ MB
None

File: tracks.jsonl
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22412 entries, 0

In [4]:
data.keys()

dict_keys(['artists.jsonl', 'sessions.jsonl', 'tracks.jsonl', 'users.jsonl'])

# Artists

In [5]:
artists_df = data['artists.jsonl']
print(artists_df.info())
print("Missing data indication:")

print(artists_df.isnull().sum())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1667 entries, 0 to 1666
Data columns (total 3 columns):
 #   Column  Non-Null Count  Dtype 
---  ------  --------------  ----- 
 0   id      1667 non-null   object
 1   name    1667 non-null   object
 2   genres  1566 non-null   object
dtypes: object(3)
memory usage: 39.2+ KB
None
Missing data indication:
id          0
name        0
genres    101
dtype: int64


In [6]:
artists_df.describe()

id       name                                             genres
count   1667       1667                                               1566
unique  1574       1667                                               1283
top       -1  Lil Nas X  [latin, latin hip hop, reggaeton, reggaeton fl...
freq      94          1                                                 15

In [7]:
from collections import Counter

genre_counter = Counter([genre for sublist in artists_df['genres'].dropna() for genre in sublist])

genre_counts_df = pd.DataFrame.from_dict(genre_counter, orient='index', columns=['count'])
genre_counts_df = genre_counts_df.reset_index().rename(columns={'index': 'genre'})
genre_counts_df.sort_values(by='count', ascending=False, inplace=True)
genre_counts_df.head(20)

genre  count
31                pop    315
4           dance pop    231
2             pop rap    150
54                rap    145
74      post-teen pop    145
24              latin    131
123              rock    131
80            hip hop    111
27        trap latino    103
55               trap     94
40          latin pop     89
8      tropical house     86
6           pop dance     83
25          reggaeton     83
5                 edm     80
72         electropop     74
64        modern rock     73
164          pop rock     71
172  southern hip hop     62
41           tropical     61

In [8]:
fig = px.bar(genre_counts_df, x='genre', y='count', labels={'genre': 'Genre', 'count': 'Count'},
             title='Count of Artists in Individual Genres')
fig.update_traces(marker_color='skyblue', marker_line_color='black', marker_line_width=1.5, opacity=0.7)
fig.update_xaxes(tickangle=45, tickfont=dict(size=9))
fig.update_layout(showlegend=False)
fig.show()

In [9]:
artists_df['num_genres'] = artists_df['genres'].apply(lambda x: len(x) if isinstance(x, list) else 0)

genre_count_per_artist = artists_df['num_genres'].value_counts().sort_index()

fig = px.bar(x=genre_count_per_artist.index, y=genre_count_per_artist.values,
             labels={'x': 'Number of Genres Assigned', 'y': 'Count of Artists'},
             title='Number of Genres Assigned per Artist')
fig.update_traces(marker_color='skyblue', marker_line_color='black', marker_line_width=1.5, opacity=0.7)
fig.update_layout(xaxis=dict(type='category'))
fig.show()

QUESTION: Dlaczego 101 artystów nie ma przypisanego gatunku? 

# Tracks

In [10]:
tracks_df = data['tracks.jsonl']
print(tracks_df.info()) 
print("Missing data indication:")
print(tracks_df.isnull().sum())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 22412 entries, 0 to 22411
Data columns (total 17 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   id                21293 non-null  object 
 1   name              21265 non-null  object 
 2   popularity        21302 non-null  float64
 3   duration_ms       22412 non-null  int64  
 4   explicit          22412 non-null  int64  
 5   id_artist         21266 non-null  object 
 6   release_date      22412 non-null  object 
 7   danceability      22412 non-null  float64
 8   energy            22412 non-null  float64
 9   key               22412 non-null  int64  
 10  loudness          22412 non-null  float64
 11  speechiness       22412 non-null  float64
 12  acousticness      22412 non-null  float64
 13  instrumentalness  22412 non-null  float64
 14  liveness          22412 non-null  float64
 15  valence           22412 non-null  float64
 16  tempo             22412 non-null  float6

In [11]:
tracks_df[tracks_df.select_dtypes(include=['number']).columns].describe()

popularity   duration_ms      explicit  danceability        energy  \
count  21302.000000  2.241200e+04  22412.000000  22412.000000  22412.000000   
mean      61.388133  2.301383e+05      0.166607      0.599096      0.648017   
std        8.052055  7.209562e+04      0.372633      0.158259      0.209577   
min       51.000000  3.062200e+04      0.000000      0.000000      0.000103   
25%       55.000000  1.914930e+05      0.000000      0.495000      0.508000   
50%       60.000000  2.206670e+05      0.000000      0.608000      0.672000   
75%       67.000000  2.562400e+05      0.000000      0.715000      0.816000   
max       99.000000  4.120258e+06      1.000000      0.980000      0.999000   

                key      loudness   speechiness  acousticness  \
count  22412.000000  22412.000000  22412.000000  22412.000000   
mean       5.278824     -7.196227      0.082914      0.267758   
std        3.558813      3.738098      0.089317      0.276111   
min        0.000000    -44.410000      0.000000      0.000001   
25%        2.000000     -8.614500      0.033900      0.029800   
50%        5.000000     -6.393000      0.046300      0.165000   
75%        8.000000     -4.850000      0.086000      0.455000   
max       11.000000      0.642000      0.944000      0.996000   

       instrumentalness      liveness       valence         tempo  
count      22412.000000  22412.000000  22412.000000  22412.000000  
mean           0.040220      0.193141      0.518000    121.911945  
std            0.152828      0.167943      0.244477     29.615254  
min            0.000000      0.012000      0.000000      0.000000  
25%            0.000000      0.094400      0.325000     97.988000  
50%            0.000003      0.125000      0.512000    120.041000  
75%            0.000523      0.240000      0.713000    140.078000  
max            0.998000      0.997000      0.991000    220.099000

In [12]:
# Selecting numerical columns for distribution plots
numerical_columns = ['popularity', 'duration_ms', 'explicit', 'danceability', 'energy',
                     'key', 'loudness', 'speechiness', 'acousticness', 'instrumentalness',
                     'liveness', 'valence', 'tempo']

# Create smaller individual distribution plots for each numerical column
for col in numerical_columns:
    fig = px.histogram(tracks_df, x=col, title=f'Distribution of {col}', opacity=0.7)
    fig.update_layout(height=300, width=300, showlegend=False,
                      xaxis_title='Value', yaxis_title='Frequency')
    fig.show()

QUESTION: Dlaczego instrumentalness jest takie dziwnie przeskalowane? normalizacja wystarczy? 
QUESTION: Instrumentalness dziwne

In [13]:
tracks_df[tracks_df.select_dtypes(include=['object']).columns].describe()

id   name               id_artist release_date
count                    21293  21265                   21266        22412
unique                   21293  17012                    1413         3907
top     0RNxWy0PC3AyH4ThH3aGK6   Home  06HL4z0CvFAxyc27GXpf02   2013-01-01
freq                         1     11                     290          268

In [14]:
for column in tracks_df.columns:
    unique_values = tracks_df[column].unique()
    print(f"Column '{column}' unique categorical values:")
    print(unique_values)
    print()

Column 'id' unique categorical values:
['0RNxWy0PC3AyH4ThH3aGK6' '2W889aLIKxULEefrleFBFI'
 '4Pnzw1nLOpDNV6MKI5ueIR' ... '1fXmDeiCb3ABt5CzkMxp4u'
 '27kcZEJvhkb1rzZS9gCpdA' '27Y1N4Q4U3EfDU5Ubw8ws2']

Column 'name' unique categorical values:
['Mack the Knife' 'Someone to Watch Over Me'
 'Nancy (With the Laughing Face) - 78rpm Version' ... 'Lotus Inn'
 'remember the mornings' "What They'll Say About Us"]

Column 'popularity' unique categorical values:
[55. 54. 53. nan 56. 60. 68. 66. 63. 57. 52. 51. 61. 58. 71. 69. 77. 67.
 65. 64. 62. 79. 75. 73. 72. 70. 59. 80. 78. 74. 76. 83. 82. 84. 81. 86.
 85. 87. 90. 88. 94. 92. 89. 97. 96. 95. 93. 91. 99. 98.]

Column 'duration_ms' unique categorical values:
[201467 198000 199000 ... 195868 202355 187601]

Column 'explicit' unique categorical values:
[0 1]

Column 'id_artist' unique categorical values:
['19eLuQmk9aCobbVDHc6eek' None '1Mxqyy3pSjf8kZZL4QVxS0' ...
 '6BrvowZBreEkXzJQMpL174' '0uGk2czvcpWQA383Im6ajf'
 '1Cj9j44XMhQeNHAwWJRCKd']

Column 'r

QUESTION: Dlaczego danceability zaczyna się od 50?

In [15]:
# Group tracks by 'id_artist' and count the number of songs for each artist
songs_per_artist = tracks_df.groupby('id_artist')['id'].count().reset_index()
songs_per_artist.columns = ['id_artist', 'num_songs']

# Sort the artists by the number of songs in descending order
songs_per_artist.sort_values(by='num_songs', ascending=False, inplace=True)

In [16]:
merged_df = pd.merge(songs_per_artist, artists_df, left_on='id_artist', right_on='id', how='left')

# Create a bar plot using Plotly with artist names
fig = px.bar(merged_df, x='name', y='num_songs', 
             labels={'name': 'Artist', 'num_songs': 'Number of Songs'},
             title='Number of Songs per Artist',
             color_discrete_sequence=px.colors.qualitative.Dark24)  # Use the same color palette
fig.update_traces(marker_color='skyblue', marker_line_color='black', marker_line_width=1.5, opacity=0.7)
fig.update_xaxes(tickangle=45, tickfont=dict(size=9))
fig.update_layout(showlegend=False)
fig.show()

QUESTION: W jakich zakresach oraz jak były mierzone te dane? Czy są one znormalizowane? 
QUESTION: Dlaczego Pan Doktor Zawistowski jest takim fanem Taylor Swift??????????

In [17]:
# Create boolean masks for missing values in different columns
missing_id = tracks_df['id'].isnull()
missing_name = tracks_df['name'].isnull()
missing_popularity = tracks_df['popularity'].isnull()
missing_id_artist = tracks_df['id_artist'].isnull()

# Count the number of rows where each combination of columns has missing values
missing_id_name = (missing_id & missing_name).sum()
missing_id_popularity = (missing_id & missing_popularity).sum()
missing_id_id_artist = (missing_id & missing_id_artist).sum()
missing_name_popularity = (missing_name & missing_popularity).sum()
missing_name_id_artist = (missing_name & missing_id_artist).sum()
missing_popularity_id_artist = (missing_popularity & missing_id_artist).sum()
missing_all = (missing_id & missing_name & missing_popularity & missing_id_artist).sum()

# Output the counts for each combination of missing values
print(f"Missing 'id' and 'name': {missing_id_name}")
print(f"Missing 'id' and 'popularity': {missing_id_popularity}")
print(f"Missing 'id' and 'id_artist': {missing_id_id_artist}")
print(f"Missing 'name' and 'popularity': {missing_name_popularity}")
print(f"Missing 'name' and 'id_artist': {missing_name_id_artist}")
print(f"Missing 'popularity' and 'id_artist': {missing_popularity_id_artist}")
print(f"Missing all: {missing_all}")


Missing 'id' and 'name': 58
Missing 'id' and 'popularity': 60
Missing 'id' and 'id_artist': 49
Missing 'name' and 'popularity': 64
Missing 'name' and 'id_artist': 63
Missing 'popularity' and 'id_artist': 51
Missing all: 0


QUESTION: Dlaczego 1146 piosenek nie ma artystów?
QUESTION: Dlaczego 1119 piosenek nie ma id?
etc

braki raczej nie skorelowane

# Users

In [18]:
users_df = data['users.jsonl']
print(users_df.info())
print("Missing data indication:")

print(users_df.isnull().sum())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 500 entries, 0 to 499
Data columns (total 7 columns):
 #   Column            Non-Null Count  Dtype  
---  ------            --------------  -----  
 0   user_id           500 non-null    int64  
 1   name              500 non-null    object 
 2   city              500 non-null    object 
 3   street            500 non-null    object 
 4   favourite_genres  471 non-null    object 
 5   premium_user      478 non-null    float64
 6   id                27 non-null     float64
dtypes: float64(2), int64(1), object(4)
memory usage: 27.5+ KB
None
Missing data indication:
user_id               0
name                  0
city                  0
street                0
favourite_genres     29
premium_user         22
id                  473
dtype: int64


QUESTION: Czym jest kolumna id (id=-1) i dlaczego tylko 27 userów ją ma?

In [19]:
from collections import Counter

genre_counter = Counter([genre for sublist in users_df['favourite_genres'].dropna() for genre in sublist])

user_genre_counts_df = pd.DataFrame.from_dict(genre_counter, orient='index', columns=['count'])
user_genre_counts_df = user_genre_counts_df.reset_index().rename(columns={'index': 'genre'})
user_genre_counts_df.sort_values(by='count', ascending=False, inplace=True)
user_genre_counts_df.head(20)

genre  count
4    latin arena pop     39
15      canadian pop     38
21           country     37
14          ranchera     36
26           corrido     36
6                rap     36
22           hip hop     35
29  alternative rock     34
16               pop     33
31     post-teen pop     32
12   adult standards     32
11  psychedelic rock     31
3          reggaeton     31
35    french hip hop     30
38   rock en espanol     30
23   k-pop boy group     30
44        neo mellow     30
25           pop rap     30
49         soft rock     30
18  regional mexican     30

In [20]:
fig = px.bar(genre_counts_df, x='genre', y='count', labels={'genre': 'Genre', 'count': 'Count'},
             title='Count of Favourite Genres among Users')
fig.update_traces(marker_color='skyblue', marker_line_color='black', marker_line_width=1.5, opacity=0.7)
fig.update_xaxes(tickangle=45, tickfont=dict(size=9))
fig.update_layout(showlegend=False)
fig.show()

In [21]:
users_df['num_genres'] = users_df['favourite_genres'].apply(lambda x: len(x) if isinstance(x, list) else 0)

genre_count_per_artist = users_df['num_genres'].value_counts().sort_index()

fig = px.bar(x=genre_count_per_artist.index, y=genre_count_per_artist.values,
             labels={'x': 'Number of Genres Assigned', 'y': 'Count of Users'},
             title='Number of Genres Assigned per User')
fig.update_traces(marker_color='skyblue', marker_line_color='black', marker_line_width=1.5, opacity=0.7)
fig.update_layout(xaxis=dict(type='category'))
fig.show()

QUESTION: Czemu 29 użytkowników nie ma przypisanych ulubionych gatunków?

### Ulubione gatunki użytkowników vs gatunki artystów

In [22]:
import pandas as pd
import plotly.graph_objs as go
from collections import Counter

def compare_genre_counts(df1, df2):
    # Flattening lists of genres in each DataFrame
    genres_df1 = [genre for sublist in df1['genres'].dropna() for genre in sublist]
    genres_df2 = [genre for sublist in df2['favourite_genres'].dropna() for genre in sublist]

    # Counting occurrences of each genre
    count_df1 = Counter(genres_df1)
    count_df2 = Counter(genres_df2)

    # Finding common and exclusive genres
    common_genres = set(count_df1.keys()).intersection(count_df2.keys())
    exclusive_to_df1 = set(count_df1.keys()) - common_genres
    exclusive_to_df2 = set(count_df2.keys()) - common_genres

    # Counting the number of each type of genres
    common_count = sum(count_df1[genre] for genre in common_genres)
    exclusive_count_df1 = sum(count_df1[genre] for genre in exclusive_to_df1)
    exclusive_count_df2 = sum(count_df2[genre] for genre in exclusive_to_df2)

    # Creating Plotly chart
    labels = ['Common Genres', 'Exclusive to Artists', 'Exclusive to Users']
    values = [common_count, exclusive_count_df1, exclusive_count_df2]

    fig = go.Figure(data=[go.Pie(labels=labels, values=values)])
    fig.update_layout(title='Comparison of Genre Counts between DataFrames')
    fig.show()

compare_genre_counts(artists_df, users_df)

QUESTION: Ponad połowa gatunków artystów nie ma użytkownika, którego ten gatunek byłby ulubionym

# Sessions

In [23]:
sessions_df = data['sessions.jsonl']
print(sessions_df.info())
print("Missing data indication:")

print(sessions_df.isnull().sum())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 759425 entries, 0 to 759424
Data columns (total 5 columns):
 #   Column      Non-Null Count   Dtype         
---  ------      --------------   -----         
 0   session_id  759425 non-null  int64         
 1   timestamp   759425 non-null  datetime64[ns]
 2   user_id     721555 non-null  float64       
 3   track_id    624016 non-null  object        
 4   event_type  721378 non-null  object        
dtypes: datetime64[ns](1), float64(1), int64(1), object(2)
memory usage: 29.0+ MB
None
Missing data indication:
session_id         0
timestamp          0
user_id        37870
track_id      135409
event_type     38047
dtype: int64


QUESTION: Ogromne braki, aż 135k eventów w sesji nie ma przypisanego track_id, a prawie 40k nie ma user_id i event_type

In [24]:
from collections import Counter

session_counter = Counter([event for event in sessions_df['event_type'].dropna()])

genre_counts_df = pd.DataFrame.from_dict(session_counter, orient='index', columns=['count'])
genre_counts_df = genre_counts_df.reset_index().rename(columns={'index': 'genre'})
genre_counts_df.sort_values(by='count', ascending=False, inplace=True)
genre_counts_df.head(20)

genre   count
0          play  399638
1          skip  124707
2          like   99642
3  advertisment   97391

In [25]:
sessions_df['timestamp'] = pd.to_datetime(sessions_df['timestamp'])

play_events = sessions_df[sessions_df['event_type'] == 'play']

# Extracting month and year from timestamp
play_events['year_month'] = play_events['timestamp'].dt.to_period('M')

# Grouping by month and year to count occurrences
play_counts = play_events.groupby('year_month').size().reset_index(name='count')

# Converting Period to string for Plotly compatibility
play_counts['year_month'] = play_counts['year_month'].astype(str)

# Plotting with Plotly
fig = px.bar(play_counts, x='year_month', y='count', labels={'year_month': 'Year-Month', 'count': 'Play Events Count'})
fig.update_layout(title='Play Events Count by Month and Year')
fig.show()

C:\Users\dziew\AppData\Local\Temp\ipykernel_9676\2826790368.py:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



QUESTION: Listopad miał mało eventów typu play. Może to być spowodowane początkami serwisu albo błędami w danych

In [26]:
import json

event_type_counts = {}
with open('./data/sessions.jsonl', 'r') as file:
    for line in file:
        data = json.loads(line)
        if data['track_id'] is None:
            event_type = data['event_type']
            if event_type in event_type_counts:
                event_type_counts[event_type] += 1
            else:
                event_type_counts[event_type] = 1

# Create a plotly bar chart
fig = px.bar(
    x=list(event_type_counts.keys()),
    y=list(event_type_counts.values()),
    labels={'x': 'Event Type', 'y': 'Count'},
    title='Count of Event Types where track_id is Null'
)

fig.show()

QUESTION: Jest łącznie 30k przypadków, gdzie track_id jest null, a nie powinien

In [27]:
event_type_counts = {}
with open('./data/sessions.jsonl', 'r') as file:
    for line in file:
        data = json.loads(line)
        if data['user_id'] is None:
            event_type = data['event_type']
            if event_type in event_type_counts:
                event_type_counts[event_type] += 1
            else:
                event_type_counts[event_type] = 1

# Create a plotly bar chart
fig = px.bar(
    x=list(event_type_counts.keys()),
    y=list(event_type_counts.values()),
    labels={'x': 'Event Type', 'y': 'Count'},
    title='Count of Event Types where user_id is Null'
)

fig.show()